In [1]:
#!gsutil -m cp gs://terra-featured-workspaces/Sc_SnRNA-seq/data/mouse_cortex/raw_feature_bc_matrix.h5 ./mouse/
#!gsutil -m cp gs://terra-featured-workspaces/Sc_SnRNA-seq/data/mouse_cortex_ADT/mouse_cortex_ADT.csv ./mouse/

In [2]:
#!sccloud demuxEM -p 8 --min-num-genes 200 --generate-diagnostic-plots ./mouse/mouse_cortex_ADT.csv ./mouse/raw_feature_bc_matrix.h5 ./mouse/exp

In [3]:
import sccloud as scc
import numpy as np

//anaconda3/envs/sccloud/lib/python3.7/site-packages/lightgbm/__init__.py:46: UserWarning: Starting from version 2.2.1, the library file in distribution wheels for macOS is built by the Apple Clang (Xcode_9.4.1) compiler.
This means that in case of installing LightGBM from PyPI via the ``pip install lightgbm`` command, you don't need to install the gcc compiler anymore.
Instead of that, you need to install the OpenMP library, which is required for running LightGBM on the system with the Apple Clang compiler.
You can install the OpenMP library by the following command: ``brew install libomp``.
  "You can install the OpenMP library by the following command: ``brew install libomp``.", UserWarning)


## Preprocessing

In [4]:
adata = scc.read_input("./mouse/exp_demux.h5sc", select_singlets = True)
adata

2019-08-28 12:16:07,570 - sccloud - INFO - Read input is finished. Time spent = 1.03s.


AnnData object with n_obs × n_vars = 3267 × 27998 
    obs: 'assignment', 'Channel'
    var: 'gene_ids'
    uns: 'genome'

In [5]:
adata.obs['assignment'].value_counts()

Sample5M    502
Sample8M    467
Sample6M    408
Sample2F    397
Sample1F    397
Sample3F    376
Sample7M    367
Sample4F    353
Name: assignment, dtype: int64

In [6]:
scc.qc_metrics(adata, mito_prefix = 'mt-', min_genes = 200)

In [7]:
adata.var.keys()

Index(['gene_ids', 'n_cells', 'percent_cells', 'robust',
       'highly_variable_features'],
      dtype='object')

In [8]:
adata.obs.keys()

Index(['assignment', 'Channel', 'passed_qc', 'n_genes', 'n_counts',
       'percent_mito'],
      dtype='object')

In [9]:
scc.violin(adata, keys = ['n_genes', 'n_counts', 'percent_mito'], by = 'passed_qc')

:Layout
   .Violin.I   :Violin   [passed_qc]   (n_genes)
   .Violin.II  :Violin   [passed_qc]   (n_counts)
   .Violin.III :Violin   [passed_qc]   (percent_mito)

In [10]:
scc.scatter_matrix(adata, ['n_genes', 'n_counts', 'percent_mito'], color='passed_qc')

:GridMatrix   [X,Y]
   :NdOverlay   [passed_qc]
      :Histogram   [percent_mito]   (percent_mito_frequency)

In [11]:
scc.violin(adata, keys = ['n_cells'])

:Layout
   .Violin.I :Violin   (n_cells)

In [12]:
scc.filter_data(adata)
adata

2019-08-28 12:16:09,611 - sccloud - INFO - After filteration, 3219 cells and 20353 genes are kept. Among 20353 genes, 18870 genes are robust.


AnnData object with n_obs × n_vars = 3219 × 20353 
    obs: 'assignment', 'Channel', 'passed_qc', 'n_genes', 'n_counts', 'percent_mito'
    var: 'gene_ids', 'n_cells', 'percent_cells', 'robust', 'highly_variable_features'
    uns: 'genome'

In [13]:
scc.log_norm(adata, norm_count = 1e5)

2019-08-28 12:16:09,751 - sccloud - INFO - Normalization is finished. Time spent = 0.13s.


In [14]:
scc.highly_variable_features(adata, consider_batch = False)

2019-08-28 12:16:09,863 - sccloud - INFO - 2000 highly variable features have been selected. Time spent = 0.10s.


In [15]:
scc.variable_feature_plot(adata)

:Overlay
   .NdOverlay.I :NdOverlay   [highly_variable_features]
      :Scatter   [mean]   (var,id)
   .Curve.I     :Curve   [mean]   (hvf_loess,id)

In [16]:
scc.pca(adata)

2019-08-28 12:16:10,456 - sccloud - INFO - PCA is done. Time spent = 0.17s.


In [17]:
scc.neighbors(adata)

2019-08-28 12:16:10,864 - sccloud - INFO - Nearest neighbor search is finished in 0.40s.
2019-08-28 12:16:10,967 - sccloud - INFO - Constructing affinity matrix is done. Time spent = 0.10s.
2019-08-28 12:16:10,967 - sccloud - INFO - Affinity matrix calculation is finished in 0.10s


## Clustering

In [18]:
scc.leiden(adata, n_iter = 2)

2019-08-28 12:16:11,077 - sccloud - INFO - Graph is constructed. Time spent = 0.10s.
2019-08-28 12:16:11,416 - sccloud - INFO - Leiden clustering is done. Time spent = 0.44s.


In [19]:
scc.composition_plot(adata, by = 'leiden_labels', condition = 'assignment')

:Layout
   .Bars.I  :Bars   [leiden_labels,assignment]   (value)
   .Table.I :Table   [cluster,fdr,bonferroni,p_value,chi2]

## Dimension Reduction

In [20]:
scc.fitsne(adata)

2019-08-28 12:16:40,908 - sccloud - INFO - FIt-SNE is calculated. Time spent = 29.31s.


In [21]:
scc.embedding(adata, basis = 'fitsne', keys = ['leiden_labels', 'assignment'])

:Layout
   .NdOverlay.I  :NdOverlay   [leiden_labels]
      :Scatter   [X_fitsne1]   (X_fitsne2,assignment)
   .NdOverlay.II :NdOverlay   [assignment]
      :Scatter   [X_fitsne1]   (X_fitsne2,leiden_labels)

In [22]:
scc.umap(adata)

UMAP(a=None, angular_rp_forest=False, b=None, init='spectral',
     learning_rate=1.0, local_connectivity=1.0, metric='euclidean',
     metric_kwds=None, min_dist=0.5, n_components=2, n_epochs=None,
     n_neighbors=15, negative_sample_rate=5, random_state=0,
     repulsion_strength=1.0, set_op_mix_ratio=1.0, spread=1.0,
     target_metric='categorical', target_metric_kwds=None,
     target_n_neighbors=-1, target_weight=0.5, transform_queue_size=4.0,
     transform_seed=42, verbose=True)
Construct fuzzy simplicial set
Wed Aug 28 12:16:41 2019 Finding Nearest Neighbors
Wed Aug 28 12:16:42 2019 Finished Nearest Neighbor Search
Wed Aug 28 12:16:43 2019 Construct embedding


//anaconda3/envs/sccloud/lib/python3.7/site-packages/umap/spectral.py:229: UserWarning: Embedding a total of 2 separate connected components using meta-embedding (experimental)
  n_components


	completed  0  /  500 epochs
	completed  50  /  500 epochs
	completed  100  /  500 epochs
	completed  150  /  500 epochs
	completed  200  /  500 epochs
	completed  250  /  500 epochs
	completed  300  /  500 epochs
	completed  350  /  500 epochs
	completed  400  /  500 epochs
	completed  450  /  500 epochs
Wed Aug 28 12:16:48 2019 Finished embedding
2019-08-28 12:16:48,288 - sccloud - INFO - using umap kNN graph 3219
2019-08-28 12:16:48,288 - sccloud - INFO - UMAP is calculated. Time spent = 6.54s.


In [23]:
scc.embedding(adata, basis = 'umap', keys = ['leiden_labels', 'assignment'])

:Layout
   .NdOverlay.I  :NdOverlay   [leiden_labels]
      :Scatter   [X_umap1]   (X_umap2,assignment)
   .NdOverlay.II :NdOverlay   [assignment]
      :Scatter   [X_umap1]   (X_umap2,leiden_labels)

In [24]:
scc.diffmap(adata)
scc.fle(adata)

2019-08-28 12:16:49,145 - sccloud - INFO - Calculating connected components is done.
2019-08-28 12:16:49,159 - sccloud - INFO - Calculating normalized affinity matrix is done.
2019-08-28 12:16:49,441 - sccloud - INFO - diffmap finished. Time spent = 0.30s.
2019-08-28 12:16:49,788 - sccloud - INFO - Nearest neighbor search is finished in 0.34s.
2019-08-28 12:16:49,841 - sccloud - INFO - Constructing affinity matrix is done. Time spent = 0.05s.
2019-08-28 12:16:49,842 - sccloud - INFO - Affinity matrix calculation is finished in 0.05s
2019-08-28 12:16:49,880 - sccloud - INFO - Graph is constructed. Time spent = 0.04s.
/var/folders/9y/7cx5sqf153gc_x672pscmn2c0000gq/T/tmpln9cyb6r.net is written.
['java', '-Djava.awt.headless=true', '-Xmx8g', '-cp', '//anaconda3/envs/sccloud/lib/python3.7/site-packages/forceatlas2/ext/forceatlas2.jar://anaconda3/envs/sccloud/lib/python3.7/site-packages/forceatlas2/ext/gephi-toolkit-0.9.2-all.jar', 'kco.forceatlas2.Main', '--input', '/var/folders/9y/7cx5sqf1

In [25]:
scc.embedding(adata, basis = 'fle', keys = ['leiden_labels', 'assignment'])

:Layout
   .NdOverlay.I  :NdOverlay   [leiden_labels]
      :Scatter   [X_fle1]   (X_fle2,assignment)
   .NdOverlay.II :NdOverlay   [assignment]
      :Scatter   [X_fle1]   (X_fle2,leiden_labels)

## Differential Expression Analysis

In [26]:
scc.de_analysis(adata, cluster = 'leiden_labels', fisher = True, mwu = True)

2019-08-28 12:17:04,493 - sccloud - INFO - Collecting basic statistics is done. Time spent = 10.54s.
2019-08-28 12:17:04,657 - sccloud - INFO - Converting X to csc_matrix is done. Time spent = 0.16s.
2019-08-28 12:17:29,001 - sccloud - INFO - AUROC values are calculated. Time spent = 24.34s.
2019-08-28 12:17:29,233 - sccloud - INFO - Welch's t-test is done. Time spent = 0.23s.
2019-08-28 12:17:30,027 - sccloud - INFO - Fisher's exact test is done. Time spent = 0.79s.
2019-08-28 12:17:45,874 - sccloud - INFO - Mann-Whitney U test is done. Time spent = 15.85s.
2019-08-28 12:17:46,037 - sccloud - INFO - Differential expression analysis is finished. Time spent = 52.10s.


Show a volcano plot for clusters 1 and 2.

In [27]:
scc.volcano(adata, cluster_ids=['1', '2'])

:Layout
   .Scatter.I  :Scatter   [log_fold_change_1]   (t_qval_1_log,1_status,id,log_fold_change_1,t_qval_1)
   .Scatter.II :Scatter   [log_fold_change_2]   (t_qval_2_log,2_status,id,log_fold_change_2,t_qval_2)

## Find Markers Using Deep Learning

In [28]:
markers = scc.find_markers(adata, label_attr = 'leiden_labels')

[1]	valid_0's multi_error: 0.0938902	valid_1's multi_error: 0.236025
Training until validation scores don't improve for 1 rounds.
[2]	valid_0's multi_error: 0.0552295	valid_1's multi_error: 0.18323
[3]	valid_0's multi_error: 0.0434933	valid_1's multi_error: 0.15528
[4]	valid_0's multi_error: 0.0303763	valid_1's multi_error: 0.136646
[5]	valid_0's multi_error: 0.0276148	valid_1's multi_error: 0.124224
[6]	valid_0's multi_error: 0.0210563	valid_1's multi_error: 0.130435
Early stopping, best iteration is:
[5]	valid_0's multi_error: 0.0276148	valid_1's multi_error: 0.124224
2019-08-28 12:18:04,242 - sccloud - INFO - LightGBM used 17.58s to train.
2019-08-28 12:18:09,092 - sccloud - INFO - find_markers took 22.49s to finish.


In [29]:
len(markers)

13

## Annotating Clusters

In [30]:
inferred_cell_type_results = scc.infer_cell_types(adata, markers = 'mouse_brain', de_test = 't')

Rename clusters using the inferred cell types

In [31]:
new_cluster_names = scc.infer_cluster_names(inferred_cell_type_results)
adata.rename_categories('leiden_labels', new_cluster_names)

In [32]:
scc.embedding(adata, basis='fitsne', keys=['leiden_labels'], labels_on_data=True, padding=(0.1, 0.01), width=600)

:Layout
   .Overlay.I :Overlay
      .NdOverlay.I :NdOverlay   [leiden_labels]
         :Scatter   [X_fitsne1]   (X_fitsne2)
      .Labels.I    :Labels   [x,y]   (text)

## Save Results

In [33]:
scc.write_output(adata, 'mouse_cortex_scc.h5ad')

... storing 'assignment' as categorical
... storing 'Channel' as categorical


2019-08-28 12:18:11,155 - sccloud - INFO - Write output is finished. Time spent = 1.50s.
